# Signal Processing (ECE-Y253)

## Electrical and Computer Engineering Department  
### University of Patras, Greece  

**Instructor:** Konstantinos Chatzilygeroudis  
**Email:** [costashatz@upatras.gr](mailto:costashatz@upatras.gr)

## Nonlinear Optimization for Signal Estimation  

In this section, we address the problem of **estimating a signal from noisy observations** using **unconstrained optimization** techniques.  
We consider two models of increasing complexity:

1. **Sinusoidal Model**  
   $\hat{y}(t; \boldsymbol{\boldsymbol{\theta}}) = A \sin(2\pi f t + \phi) + b$

   where the parameter vector is $\boldsymbol{\boldsymbol{\theta}} = [A, f, \phi, b]^\top$.

3. **One-Hidden-Layer Neural Network Model**  
   $\hat{y}(t; \boldsymbol{\boldsymbol{\theta}}) = \boldsymbol{w_2}^\top \tanh(\boldsymbol{w_1} t + \boldsymbol{b_1}) + b_2$

   where $\boldsymbol{\boldsymbol{\theta}} = \{\boldsymbol{w_1}, \boldsymbol{b_1}, \boldsymbol{w_2}, b_2\}$ represents the full parameter set.

### Objectives

For **both** models, we:

- **Write down the mathematical formulation**:  
  - Compute residuals, gradients, and Jacobians.  
  - Derive the **Gauss–Newton system** and explain its relationship to second-order optimization.  
- **Implement and compare optimization algorithms**:  
  - **Gauss–Newton method** with **Armijo backtracking line search**.  
  - **Gradient Descent**.  
  - **Adam optimizer**, illustrating its adaptive first-order nature.  
- **Analyze performance**:  
  - Compare convergence behavior, computational efficiency, and sensitivity to initialization.  
  - Visualize learning curves and parameter trajectories.

### Learning Outcomes

By completing this exercise, you will:

- Understand how nonlinear optimization methods apply to both parametric and neural models.  
- Gain hands-on experience implementing and tuning first- and second-order optimization algorithms.  
- Appreciate the differences between deterministic (Gauss–Newton) and adaptive (Adam) optimization strategies in signal estimation tasks.


In [ ]:
# But let's first generate some data!
import numpy as np
import matplotlib.pyplot as plt

np.random.seed(123)

# Generate noisy sinusoid data
N = 500
t = np.linspace(0, 1.0, N)
A_true, f_true, phi_true, b_true = 1.2, 4.0, 0.6, 0.2
noise_std = 0.12
y = A_true*np.sin(2*np.pi*f_true*t + phi_true) + b_true + noise_std*np.random.randn(N)

plt.figure(figsize=(8,3))
plt.plot(t, y, '.', ms=2, label='y (noisy)')
plt.xlabel("time [s]"); plt.ylabel("amplitude"); plt.title("Noisy observations")
plt.legend(); plt.show()


## Sinusoid Model — Mathematical Formulation & Derivations

### Model Definition

We consider a **sinusoidal (parameteic) signal model** of the form

$
\hat{y}(t_k; \boldsymbol{\theta}) = A \sin(2\pi f t_k + \phi) + b,
$

where the parameter vector is $\boldsymbol{\theta} = [A, f, \phi, b]^\top.$

Given $N$ noisy observations $\{(t_k, y_k)\}_{k=1}^N$, we define the **residuals**

$r_k(\boldsymbol{\theta}) = y_k - \hat{y}(t_k; \boldsymbol{\theta}),$

and stack them into a residual vector

$r(\boldsymbol{\theta}) = [r_1(\boldsymbol{\theta}), \ldots, r_N(\boldsymbol{\theta})]^\top \in \mathbb{R}^N.$

### Optimization Problem

The goal is to estimate the parameters $\boldsymbol{\theta}$ that minimize the **sum of squared residuals**:

$
\min_{\boldsymbol{\theta}} J(\boldsymbol{\theta}), \quad \text{where} \quad 
J(\boldsymbol{\theta}) = \frac{1}{2} \|r(\boldsymbol{\theta})\|_2^2 = \frac{1}{2} \sum_{k=1}^N r_k(\boldsymbol{\theta})^2.
$

This is a **nonlinear least squares problem**, since the residuals depend nonlinearly on $\boldsymbol{\theta}$ through the sinusoidal model.

### Gradient Computation

By the chain rule, the gradient of the cost function is:

$
\nabla J(\boldsymbol{\theta}) = -\sum_{k=1}^N r_k(\boldsymbol{\theta}) \, \nabla_{\boldsymbol{\theta}} \hat{y}(t_k; \boldsymbol{\theta})
= \left[ \frac{\partial J}{\partial A}, \frac{\partial J}{\partial f}, \frac{\partial J}{\partial \phi}, \frac{\partial J}{\partial b} \right]^\top.
$

Let $\omega_k = 2\pi f t_k + \phi$. The partial derivatives of the residual $r_k(\boldsymbol{\theta})$ with respect to each parameter are:

$
\begin{aligned}
\frac{\partial r_k}{\partial A} &= -\sin(\omega_k), \\
\frac{\partial r_k}{\partial f} &= -A (2\pi t_k) \cos(\omega_k), \\
\frac{\partial r_k}{\partial \phi} &= -A \cos(\omega_k), \\
\frac{\partial r_k}{\partial b} &= -1.
\end{aligned}
$

Hence, the full gradient becomes:

$
\nabla J(\boldsymbol{\theta}) = \sum_{k=1}^N r_k(\boldsymbol{\theta})
\begin{bmatrix}
\sin(\omega_k) \\
A (2\pi t_k) \cos(\omega_k) \\
A \cos(\omega_k) \\
1
\end{bmatrix}.
$

### Gauss–Newton Method (GN)

The **Gauss–Newton method** approximates the Hessian of $J(\boldsymbol{\theta})$ by neglecting second-order terms, yielding:

$H_{GN}(\boldsymbol{\theta}) \approx \nabla r(\boldsymbol{\theta})^\top \nabla r(\boldsymbol{\theta}),$

where $\nabla r(\boldsymbol{\theta})$ is the matrix of partial derivatives of all residuals with respect to $\boldsymbol{\theta}$.  

The **search direction** $p$ is obtained by solving:

$H_{GN}(\boldsymbol{\theta}) \, p = \nabla r(\boldsymbol{\theta})^\top r(\boldsymbol{\theta}).$

The parameter update rule is:

$\boldsymbol{\theta} \leftarrow \boldsymbol{\theta} - \alpha p,$

where $\alpha > 0$ is determined via **Armijo backtracking** (see below).

### Gradient Descent (GD)

In **Gradient Descent**, the update rule follows the negative gradient direction:

$\boldsymbol{\theta} \leftarrow \boldsymbol{\theta} - \alpha \, \nabla J(\boldsymbol{\theta}),$

where $\alpha$ is chosen as a small constant step size. This method is simple but may converge slowly when the cost surface is ill-conditioned.

### Adam Optimizer

The **Adam** (Adaptive Moment Estimation) algorithm combines ideas from momentum and RMSProp to adapt learning rates for each parameter.  
At each iteration $t$:

$
\begin{aligned}
m_t &= \beta_1 m_{t-1} + (1 - \beta_1) \nabla J(\boldsymbol{\theta}_t), \\
v_t &= \beta_2 v_{t-1} + (1 - \beta_2) [\nabla J(\boldsymbol{\theta}_t)]^2, \\
\hat{m}_t &= \frac{m_t}{1 - \beta_1^t}, \quad
\hat{v}_t = \frac{v_t}{1 - \beta_2^t}, \\
\boldsymbol{\theta}_{t+1} &= \boldsymbol{\theta}_t - \alpha \, \frac{\hat{m}_t}{\sqrt{\hat{v}_t} + \varepsilon}.
\end{aligned}
$

Typical values are $\beta_1 = 0.9$, $\beta_2 = 0.999$, and $\varepsilon = 10^{-8}$.  
Adam adapts the effective step size per parameter, improving robustness to scaling and initialization.

### Armijo Backtracking Line Search

To ensure **sufficient decrease** in the cost function, we select the step size $\alpha$ by satisfying the **Armijo condition**:

$J(\boldsymbol{\theta} - \alpha p) \le J(\boldsymbol{\theta}) - c \, \alpha \, \nabla J(\boldsymbol{\theta})^\top p,$

where $c \in (0, 10^{-1})$ is a small constant (e.g., $c = 10^{-4}$).  
The algorithm starts with an initial step size $\alpha_0$ (e.g., $\alpha_0 = 1$) and iteratively reduces it (e.g., $\alpha \leftarrow \beta \alpha$ with $\beta \in (0,1)$, such as $0.5$) until the condition holds.

This approach balances **progress** (large steps) and **stability** (avoiding divergence).

---

### Summary

| Method | Update Rule | Step Size Selection | Notes |
|:--|:--|:--|:--|
| **Gauss–Newton** | $\boldsymbol{\theta} \leftarrow \boldsymbol{\theta} - \alpha H_{GN}^{-1}\nabla J$ | Armijo backtracking | Fast near optimum, requires Jacobians |
| **Gradient Descent** | $\boldsymbol{\theta} \leftarrow \boldsymbol{\theta} - \alpha \nabla J$ | Fixed (or externally adapted; e.g. with Armijo) | Simple but sensitive to $\alpha$ |
| **Adam** | Adaptive moment-based | Internal adaptive scheme | Robust to scaling and initialization |

---



In [ ]:
# Now let's define our function, and derivatives
def sinusoid(t, theta):
    A, f, phi, b = theta
    return A*np.sin(2*np.pi*f*t + phi) + b

def r_sinusoid(theta, t, y):
    return y - sinusoid(t, theta)

def J_sinusoid(theta, t):
    A, f, phi, b = theta
    omega = 2*np.pi*f*t + phi
    J = np.empty((t.size, 4))
    J[:,0] = -np.sin(omega)                 # dr/dA
    J[:,1] = -A*np.cos(omega) * (2*np.pi*t) # dr/df
    J[:,2] = -A*np.cos(omega)               # dr/dphi
    J[:,3] = -1.0                           # dr/db
    return J

def cost_from_r(r):
    return 0.5*np.dot(r, r)

def grad_from_Jr_r(Jr, r):
    return Jr.T @ r



### Optimizers for the sinusoid

- **GN + Armijo:** second-order (approx.) direction, robust step size.
- **Gradient Descent (GD):** first-order; optionally with Armijo.
- **Adam:** adaptive first-order; no line search.


In [ ]:

def armijo_backtracking(cost_func, grad_func, theta, p, *args, c=1e-4, beta=0.5, max_backtracks=30):
    g = grad_func(theta, *args)
    f0 = cost_func(theta, *args)
    alpha = 1.0
    for _ in range(max_backtracks):
        trial = theta - alpha * p
        if cost_func(trial, *args) <= f0 - c * alpha * np.dot(g, p):
            return alpha
        alpha *= beta
    return alpha

def gn_armijo(theta0, r_fun, J_fun, t, y, maxit=50, tol=1e-10, damping=0.0, verbose=False):
    theta = theta0.astype(float).copy()
    hist = []
    def cost_wrap(th, t_, y_):
        return cost_from_r(r_fun(th, t_, y_))
    def grad_wrap(th, t_, y_):
        r = r_fun(th, t_, y_)
        Jr = J_fun(th, t_)
        return grad_from_Jr_r(Jr, r)
    for k in range(maxit):
        r = r_fun(theta, t, y)
        Jr = J_fun(theta, t)
        g = Jr.T @ r
        H_approx = Jr.T @ Jr + damping*np.eye(Jr.shape[1])
        p = np.linalg.solve(H_approx, g)
        alpha = armijo_backtracking(cost_wrap, grad_wrap, theta, p, t, y)
        hist.append(cost_from_r(r))
        if verbose:
            print(f"[GN] iter {k:2d}  cost={hist[-1]:.6f}  ||p||={np.linalg.norm(p):.3e}  alpha={alpha:.2e}")
        if np.linalg.norm(alpha*p) < tol:
            break
        theta = theta - alpha * p
    return theta, np.array(hist)

def gd(theta0, r_fun, J_fun, t, y, lr=1e-3, maxit=2000, tol=1e-10, armijo=False, verbose=False):
    theta = theta0.astype(float).copy()
    hist = []
    def cost_wrap(th, t_, y_):
        return cost_from_r(r_fun(th, t_, y_))
    def grad_wrap(th, t_, y_):
        r = r_fun(th, t_, y_)
        Jr = J_fun(th, t_)
        return grad_from_Jr_r(Jr, r)
    for k in range(maxit):
        g = grad_wrap(theta, t, y)
        hist.append(cost_wrap(theta, t, y))
        if armijo:
            alpha = armijo_backtracking(cost_wrap, grad_wrap, theta, g, t, y)
        else:
            alpha = lr
        if verbose and k % 200 == 0:
            print(f"[GD] iter {k:4d}  cost={hist[-1]:.6f}  ||g||={np.linalg.norm(g):.3e}  alpha={alpha:.2e}")
        if np.linalg.norm(alpha*g) < tol:
            break
        theta = theta - alpha * g
    return theta, np.array(hist)

def adam(theta0, r_fun, J_fun, t, y, lr=5e-3, beta1=0.9, beta2=0.999, eps=1e-8, maxit=4000, tol=1e-10, verbose=False):
    theta = theta0.astype(float).copy()
    m = np.zeros_like(theta)
    v = np.zeros_like(theta)
    hist = []
    def cost_wrap(th, t_, y_):
        return cost_from_r(r_fun(th, t_, y_))
    def grad_wrap(th, t_, y_):
        r = r_fun(th, t_, y_)
        Jr = J_fun(th, t_)
        return grad_from_Jr_r(Jr, r)
    for k in range(1, maxit+1):
        g = grad_wrap(theta, t, y)
        hist.append(cost_wrap(theta, t, y))
        m = beta1*m + (1-beta1)*g
        v = beta2*v + (1-beta2)*(g*g)
        mhat = m/(1-beta1**k)
        vhat = v/(1-beta2**k)
        step = lr * mhat / (np.sqrt(vhat) + eps)
        if verbose and k % 400 == 0:
            print(f"[Adam] iter {k:4d}  cost={hist[-1]:.6f}  ||step||={np.linalg.norm(step):.3e}")
        if np.linalg.norm(step) < tol:
            break
        theta = theta - step
    return theta, np.array(hist)


### Initialization and Runs (Sinusoid Model)

Accurate initialization is crucial for nonlinear least squares problems, since the **cost surface** may contain multiple local minima, especially along the **frequency** dimension.  
To improve convergence reliability, we obtain a good initial estimate through a **coarse frequency scan** combined with a **linear least-squares fit** for the amplitude, phase, and bias.

#### Model Reformulation

The sinusoid model is:

$\hat{y}(t; \boldsymbol{\theta}) = A \sin(2\pi f t + \phi) + b.$

Using the trigonometric identity

$A \sin(2\pi f t + \phi) = \alpha \sin(2\pi f t) + \beta \cos(2\pi f t),$

we can rewrite the model as a **linear-in-parameters** form:

$\hat{y}(t; \alpha, \beta, b, f) = \alpha \sin(2\pi f t) + \beta \cos(2\pi f t) + b,$

where

$\alpha = A \cos(\phi), \qquad \beta = A \sin(\phi).$

#### The Linear Least Squares Problem (for Fixed Frequency)

For a fixed frequency $f$, the model becomes **linear** in $(\alpha, \beta, b)$.  
Given data $\{(t_k, y_k)\}_{k=1}^N$, we can express it compactly as:

$\mathbf{y} \approx \Phi(f)\begin{bmatrix} \alpha \\ \beta \\ b \end{bmatrix},$

where

$
\Phi(f) =
\begin{bmatrix}
\sin(2\pi f t_1) & \cos(2\pi f t_1) & 1 \\
\sin(2\pi f t_2) & \cos(2\pi f t_2) & 1 \\
\vdots & \vdots & \vdots \\
\sin(2\pi f t_N) & \cos(2\pi f t_N) & 1
\end{bmatrix}
\in \mathbb{R}^{N \times 3}.
$

We solve the **linear least squares problem**:

$\min_{\alpha, \beta, b} \; \|\mathbf{y} - \Phi(f)
\begin{bmatrix} \alpha \\ \beta \\ b \end{bmatrix}\|_2^2.
$

The solution is given in closed form by:

$
\begin{bmatrix} \alpha^*(f) \\ \beta^*(f) \\ b^*(f) \end{bmatrix}
= (\Phi(f)^\top \Phi(f))^{-1} \Phi(f)^\top \mathbf{y}.
$

#### Frequency Scan

We perform a **coarse frequency grid search**:

1. Define a set of candidate frequencies:

   $f_i \in [f_{\min}, f_{\max}], \quad i = 1, \dots, N_f.$
2. For each $f_i$:
   - Build $\Phi(f_i)$.
   - Solve the above linear least squares problem.
   - Compute the **fit quality**:

     $E(f_i) = \|\mathbf{y} - \Phi(f_i)
     \begin{bmatrix} \alpha^*(f_i) \\ \beta^*(f_i) \\ b^*(f_i) \end{bmatrix}\|_2^2.$
3. Choose the frequency with **minimum residual error**:

   $f_0 = \arg\min_{f_i} E(f_i).$

#### Recovering Nonlinear Parameters

After determining $f_0$, we convert the linear parameters $(\alpha, \beta, b)$ into the original sinusoidal parameters:

$A_0 = \sqrt{\alpha^{*2}(f_0) + \beta^{*2}(f_0)}, \qquad
\phi_0 = \arctan2(\beta^*(f_0), \alpha^*(f_0)), \qquad
b_0 = b^*(f_0).$

Thus, the initial parameter vector is:

$\boldsymbol{\theta}_0 = [A_0, f_0, \phi_0, b_0]^\top.$

#### Summary of the Procedure

| Step | Description |
|:--|:--|
| 1 | Generate candidate frequencies $f_i$ in $[f_{\min}, f_{\max}]$. |
| 2 | For each $f_i$, solve the linear least squares problem for $(\alpha, \beta, b)$. |
| 3 | Evaluate the residual error $E(f_i)$. |
| 4 | Select the $f_i$ minimizing $E(f_i)$. |
| 5 | Convert $(\alpha, \beta, b)$ to $(A, \phi, b)$ to form $\boldsymbol{\theta}_0$. |

---

#### Why This Works

- The model is **nonlinear in $f$** but **linear in $\alpha, \beta, b$**.  
- The frequency scan converts the nonlinear problem into a sequence of **linear least squares** subproblems.  
- The selected frequency minimizes the overall residual energy, yielding a **near-optimal initialization** that avoids poor local minima.  
- This initialization dramatically improves the convergence of **Gauss–Newton**, **Gradient Descent**, and **Adam** methods.


In [ ]:
def init_guess_sinusoid(t, y, f_min=0.1, f_max=20.0, num=2000):
    freqs = np.linspace(f_min, f_max, num)
    scores = []
    for f in freqs:
        s = np.sin(2*np.pi*f*t)
        c = np.cos(2*np.pi*f*t)
        Phi = np.column_stack([s, c, np.ones_like(t)])
        theta_lin, *_ = np.linalg.lstsq(Phi, y, rcond=None)
        y_hat = Phi @ theta_lin
        scores.append(-np.sum((y - y_hat)**2))
    f0 = freqs[np.argmax(scores)]
    s = np.sin(2*np.pi*f0*t); c = np.cos(2*np.pi*f0*t)
    Phi = np.column_stack([s, c, np.ones_like(t)])
    alpha, beta, b = np.linalg.lstsq(Phi, y, rcond=None)[0]
    A0 = np.sqrt(alpha**2 + beta**2)
    phi0 = np.arctan2(beta, alpha)
    return np.array([A0, f0, phi0, b])

theta0_good = init_guess_sinusoid(t, y)
theta0_poor = theta0_good.copy()
theta0_poor[1] *= 0.35
theta0_poor[2] += 2.0

theta_gn_good, hist_gn_good = gn_armijo(theta0_good, r_sinusoid, J_sinusoid, t, y, damping=1e-8, verbose=False)
theta_gd_good, hist_gd_good = gd(theta0_good, r_sinusoid, J_sinusoid, t, y, lr=2e-4, armijo=False, maxit=6000)
theta_gdA_good, hist_gdA_good = gd(theta0_good, r_sinusoid, J_sinusoid, t, y, armijo=True, maxit=4000)
theta_adam_good, hist_adam_good = adam(theta0_good, r_sinusoid, J_sinusoid, t, y, lr=5e-3, maxit=6000)

theta_gn_poor, hist_gn_poor = gn_armijo(theta0_poor, r_sinusoid, J_sinusoid, t, y, damping=1e-8, verbose=False)
theta_gd_poor, hist_gd_poor = gd(theta0_poor, r_sinusoid, J_sinusoid, t, y, lr=2e-4, armijo=False, maxit=6000)
theta_gdA_poor, hist_gdA_poor = gd(theta0_poor, r_sinusoid, J_sinusoid, t, y, armijo=True, maxit=4000)
theta_adam_poor, hist_adam_poor = adam(theta0_poor, r_sinusoid, J_sinusoid, t, y, lr=5e-3, maxit=6000)

print("True:           A=%.3f f=%.3f phi=%.3f b=%.3f" % (A_true, f_true, phi_true, b_true))
print("Init (good):    A=%.3f f=%.3f phi=%.3f b=%.3f" % tuple(theta0_good))
print("GN (good):      A=%.3f f=%.3f phi=%.3f b=%.3f" % tuple(theta_gn_good))
print("GD (good):      A=%.3f f=%.3f phi=%.3f b=%.3f" % tuple(theta_gd_good))
print("GD+Armijo(good):A=%.3f f=%.3f phi=%.3f b=%.3f" % tuple(theta_gdA_good))
print("Adam (good):    A=%.3f f=%.3f phi=%.3f b=%.3f" % tuple(theta_adam_good))
print()
print("Init (poor):    A=%.3f f=%.3f phi=%.3f b=%.3f" % tuple(theta0_poor))
print("GN (poor):      A=%.3f f=%.3f phi=%.3f b=%.3f" % tuple(theta_gn_poor))
print("GD (poor):      A=%.3f f=%.3f phi=%.3f b=%.3f" % tuple(theta_gd_poor))
print("GD+Armijo(poor):A=%.3f f=%.3f phi=%.3f b=%.3f" % tuple(theta_gdA_poor))
print("Adam (poor):    A=%.3f f=%.3f phi=%.3f b=%.3f" % tuple(theta_adam_poor))

plt.figure(figsize=(8,3))
plt.plot(t, y, '.', ms=2, label='y')
plt.plot(t, sinusoid(t, theta_gn_good), label='GN good')
plt.plot(t, sinusoid(t, theta_adam_good), label='Adam good')
plt.plot(t, sinusoid(t, theta_gdA_good), label='GD+Armijo good')
plt.legend(); plt.title("Sinusoid fits (good init)"); plt.show()

plt.figure(figsize=(8,3))
plt.plot(t, y, '.', ms=2, label='y')
plt.plot(t, sinusoid(t, theta_gn_poor), label='GN poor')
plt.plot(t, sinusoid(t, theta_adam_poor), label='Adam poor')
plt.plot(t, sinusoid(t, theta_gdA_poor), label='GD+Armijo poor')
plt.legend(); plt.title("Sinusoid fits (poor init)"); plt.show()

plt.figure(figsize=(6,3))
plt.semilogy(hist_gn_good, label='GN good')
plt.semilogy(hist_gd_good, label='GD good')
plt.semilogy(hist_gdA_good, label='GD+Armijo good')
plt.semilogy(hist_adam_good, label='Adam good')
plt.xlabel("iteration"); plt.ylabel("cost"); plt.title("Convergence (good init)"); plt.legend(); plt.show()

plt.figure(figsize=(6,3))
plt.semilogy(hist_gn_poor, label='GN poor')
plt.semilogy(hist_gd_poor, label='GD poor')
plt.semilogy(hist_gdA_poor, label='GD+Armijo poor')
plt.semilogy(hist_adam_poor, label='Adam poor')
plt.xlabel("iteration"); plt.ylabel("cost"); plt.title("Convergence (poor init)"); plt.legend(); plt.show()


## One-Hidden-Layer Neural Network Model — Mathematical Formulation & Derivations

### Model Definition (Scalar Input)

We now consider a **nonlinear regression model** based on a **one-hidden-layer neural network** with a scalar input $t$ and a scalar output $\hat{y}$:

$\hat{y}(t; \boldsymbol{\theta}) = \boldsymbol{w_2}^\top h + b_2, \quad h = \tanh(z), \quad z = \boldsymbol{w_1} t + \boldsymbol{b_1},$

where:
- $\boldsymbol{w_1} \in \mathbb{R}^{m}$ are the **input-to-hidden weights**,  
- $\boldsymbol{b_1} \in \mathbb{R}^m$ are the **hidden biases**,  
- $\boldsymbol{w_2} \in \mathbb{R}^m$ are the **hidden-to-output weights**,  
- $b_2 \in \mathbb{R}$ is the **output bias**,  
- and $\tanh(\cdot)$ is applied elementwise.

We group all parameters into a single vector:

$\boldsymbol{\theta} = [\boldsymbol{w_1}, \; \boldsymbol{b_1}, \; \boldsymbol{w_2}, \; b_2]^\top \in \mathbb{R}^{3m+1}.$

### Optimization Problem

Given $N$ training pairs $\{(t_k, y_k)\}_{k=1}^N$, the objective is to minimize the **sum of squared residuals** between the network predictions and measured data:

$\min_{\boldsymbol{\theta}} J(\boldsymbol{\theta}), \quad \text{where} \quad 
J(\boldsymbol{\theta}) = \frac{1}{2} \sum_{k=1}^N r_k(\boldsymbol{\theta})^2,$

with residuals defined as:

$r_k(\boldsymbol{\theta}) = y_k - \hat{y}(t_k; \boldsymbol{\theta}).$

This is again a **nonlinear least squares** problem, since $\hat{y}$ depends nonlinearly on $\boldsymbol{\theta}$ through the $\tanh$ activation.

### Activation and Its Derivative

Let $\sigma(u) = \tanh(u)$ and note that:

$\sigma'(u) = 1 - \tanh^2(u) = 1 - \sigma(u)^2.$

This derivative plays a key role in computing the gradient of the residuals — analogous to **backpropagation** in neural networks.

### Gradient and Partial Derivatives of Residuals

For a single data point $(t_k, y_k)$, define:

$z_i(t_k) = w_{1,i} t_k + b_{1,i}, \quad h_i(t_k) = \tanh(z_i(t_k)).$

Then, the predicted output is:

$\hat{y}(t_k; \boldsymbol{\theta}) = \sum_{i=1}^m w_{2,i} \, h_i(t_k) + b_2.$

The residual is:

$r_k(\boldsymbol{\theta}) = y_k - \hat{y}(t_k; \boldsymbol{\theta}).$

By applying the chain rule, the per-parameter partial derivatives of the residual are:

$
\begin{aligned}
\frac{\partial r_k}{\partial w_{2,i}} &= -h_i(t_k), \\
\frac{\partial r_k}{\partial b_2} &= -1, \\
\frac{\partial r_k}{\partial W_{1,i}} &= -w_{2,i} \, \sigma'(z_i(t_k)) \, t_k, \\
\frac{\partial r_k}{\partial b_{1,i}} &= -w_{2,i} \, \sigma'(z_i(t_k)).
\end{aligned}
$

These expressions form the **gradient of each residual** with respect to all parameters.  

Stacking over all samples yields the **Jacobian of residuals**:

$
\nabla r(\boldsymbol{\theta}) = 
\begin{bmatrix}
(\nabla_{\boldsymbol{\theta}} r_1(\boldsymbol{\theta}))^\top \\
\vdots \\
(\nabla_{\boldsymbol{\theta}} r_N(\boldsymbol{\theta}))^\top
\end{bmatrix}
\in \mathbb{R}^{N \times (3m+1)}.
$

### Gradient of the Cost Function

Using the standard result from nonlinear least squares, the gradient of the total cost is:

$\nabla J(\boldsymbol{\theta}) = \nabla r(\boldsymbol{\theta})^\top r(\boldsymbol{\theta}) 
= \sum_{k=1}^N r_k(\boldsymbol{\theta}) \, \nabla_{\boldsymbol{\theta}} r_k(\boldsymbol{\theta}).$

This is the **backpropagation rule** for this simple network — it accumulates contributions from each sample via the chain rule.

### Gauss–Newton Approximation

The **Gauss–Newton (GN)** method approximates the Hessian matrix by neglecting the second-order derivative terms of the residuals. The approximate Hessian is:

$H_{GN}(\boldsymbol{\theta}) \approx \nabla r(\boldsymbol{\theta})^\top \nabla r(\boldsymbol{\theta}).$

The **search direction** $p$ is obtained by solving the **normal equations**:

$H_{GN}(\boldsymbol{\theta}) \, p = \nabla r(\boldsymbol{\theta})^\top r(\boldsymbol{\theta}).$

Then the parameters are updated as:

$\boldsymbol{\theta} \leftarrow \boldsymbol{\theta} - \alpha p,$

where $\alpha > 0$ is chosen via **Armijo backtracking line search** to ensure sufficient decrease of $J(\boldsymbol{\theta})$.

### Gradient Descent and Adam

As in the sinusoidal case, we can also use **Gradient Descent (GD)** or **Adam** to minimize $J(\boldsymbol{\theta})$:

- **Gradient Descent (GD):**

  $\boldsymbol{\theta} \leftarrow \boldsymbol{\theta} - \alpha \, \nabla J(\boldsymbol{\theta}),$

  with either a fixed or backtracked step size $\alpha$.

- **Adam (Adaptive Moment Estimation):**
  Adaptive learning rate updates per parameter using exponential moving averages of first and second moments of the gradient:

  $\begin{aligned}
  m_t &= \beta_1 m_{t-1} + (1 - \beta_1) \nabla J(\boldsymbol{\theta}_t), \\
  v_t &= \beta_2 v_{t-1} + (1 - \beta_2) [\nabla J(\boldsymbol{\theta}_t)]^2, \\
  \hat{m}_t &= \frac{m_t}{1 - \beta_1^t}, \quad
  \hat{v}_t = \frac{v_t}{1 - \beta_2^t}, \\
  \boldsymbol{\theta}_{t+1} &= \boldsymbol{\theta}_t - \alpha \, \frac{\hat{m}_t}{\sqrt{\hat{v}_t} + \varepsilon}.
  \end{aligned}
  $

Adam is more robust to poor scaling and often converges faster on neural networks, though it does not directly exploit second-order curvature information.

### Remarks

- The one-hidden-layer NN model is a **universal approximator**; even with few hidden units, it can represent a wide range of nonlinear signals.  
- However, the optimization landscape is highly **nonconvex**, so initialization and proper step size control (e.g., Armijo) are important.  
- The **Gauss–Newton** method captures curvature information from the Jacobian, often leading to faster convergence near a minimum, while **Adam** offers robust performance across different scales and initializations.

### Summary Table

| Symbol | Meaning | Dimensions |
|:--|:--|:--|
| $t_k, y_k$ | Input–output training pair | scalar |
| $\boldsymbol{w_1}$ | Input-to-hidden weights | $\mathbb{R}^{m\times1}$ |
| $\boldsymbol{b_1}$ | Hidden layer biases | $\mathbb{R}^m$ |
| $\boldsymbol{w_2}$ | Hidden-to-output weights | $\mathbb{R}^m$ |
| $b_2$ | Output bias | $\mathbb{R}$ |
| $\boldsymbol{\theta}$ | Parameter vector | $\mathbb{R}^{3m+1}$ |
| $r_k(\boldsymbol{\theta})$ | Residual for sample $k$ | scalar |
| $\nabla r(\boldsymbol{\theta})$ | Jacobian of residuals | $\mathbb{R}^{N\times(3m+1)}$ |


In [ ]:

def pack_nn(W1, b1, w2, b2):
    return np.concatenate([W1.flatten(), b1, w2, np.array([b2])])

def unpack_nn(theta, m):
    W1 = theta[:m].reshape(m,1)
    b1 = theta[m:2*m]
    w2 = theta[2*m:3*m]
    b2 = theta[-1]
    return W1, b1, w2, b2

def nn_forward_all(t, W1, b1, w2, b2):
    z = W1 @ t.reshape(1,-1) + b1.reshape(-1,1)  # (m,N)
    h = np.tanh(z)                               # (m,N)
    yhat = w2 @ h + b2                           # (N,)
    return yhat, z, h

def r_nn(theta, t, y, m):
    W1, b1, w2, b2 = unpack_nn(theta, m)
    yhat, _, _ = nn_forward_all(t, W1, b1, w2, b2)
    return y - yhat

def J_nn(theta, t, m):
    W1, b1, w2, b2 = unpack_nn(theta, m)
    z = W1 @ t.reshape(1,-1) + b1.reshape(-1,1)
    h = np.tanh(z)
    sech2 = 1.0 - h**2
    N = t.size
    P = 3*m + 1
    Jr = np.zeros((N, P))
    for k in range(N):
        tk = t[k]
        dW1 =  (w2 * sech2[:,k]) * tk
        db1 =   w2 * sech2[:,k]
        dw2 =   h[:,k]
        db2 =   1.0
        Jr[k,:] = np.concatenate([-dW1, -db1, -dw2, np.array([-db2])])
    return Jr

def cost_nn(theta, t, y, m):
    r = r_nn(theta, t, y, m)
    return 0.5*np.dot(r, r)

def grad_nn(theta, t, y, m):
    r = r_nn(theta, t, y, m)
    Jr = J_nn(theta, t, m)
    return Jr.T @ r


In [ ]:

def armijo_backtracking_nn(cost_func, grad_func, theta, p, t, y, m, c=1e-4, beta=0.5, max_backtracks=30):
    g = grad_func(theta, t, y, m)
    f0 = cost_func(theta, t, y, m)
    alpha = 1.0
    for _ in range(max_backtracks):
        trial = theta - alpha * p
        if cost_func(trial, t, y, m) <= f0 - c * alpha * np.dot(g, p):
            return alpha
        alpha *= beta
    return alpha

def gn_armijo_nn(theta0, t, y, m, maxit=100, tol=1e-10, damping=0.0, verbose=False):
    theta = theta0.astype(float).copy()
    hist = []
    for k in range(maxit):
        r = r_nn(theta, t, y, m)
        Jr = J_nn(theta, t, m)
        g = Jr.T @ r
        H_approx = Jr.T @ Jr + damping*np.eye(Jr.shape[1])
        p = np.linalg.solve(H_approx, g)
        alpha = armijo_backtracking_nn(cost_nn, grad_nn, theta, p, t, y, m)
        hist.append(cost_nn(theta, t, y, m))
        if verbose and k % 5 == 0:
            print(f"[NN-GN] iter {k:3d}  cost={hist[-1]:.6f}  ||p||={np.linalg.norm(p):.3e}  alpha={alpha:.2e}")
        if np.linalg.norm(alpha*p) < tol:
            break
        theta = theta - alpha * p
    return theta, np.array(hist)

def gd_nn(theta0, t, y, m, lr=1e-3, maxit=4000, tol=1e-10, verbose=False):
    theta = theta0.astype(float).copy()
    hist = []
    for k in range(maxit):
        g = grad_nn(theta, t, y, m) + 0.01 * theta
        hist.append(cost_nn(theta, t, y, m))
        if verbose and k % 1000 == 0:
            print(f"[NN-GD] iter {k:4d}  cost={hist[-1]:.6f}  ||g||={np.linalg.norm(g):.3e}  alpha={lr:.2e}")
        if np.linalg.norm(lr*g) < tol:
            break
        theta = theta - lr * g
    return theta, np.array(hist)

def adam_nn(theta0, t, y, m, lr=3e-3, beta1=0.9, beta2=0.999, eps=1e-8, maxit=6000, tol=1e-10, verbose=False):
    theta = theta0.astype(float).copy()
    M = theta.size
    m1 = np.zeros(M)
    m2 = np.zeros(M)
    hist = []
    for k in range(1, maxit+1):
        g = grad_nn(theta, t, y, m) + 0.01 * theta
        hist.append(cost_nn(theta, t, y, m))
        m1 = beta1*m1 + (1-beta1)*g
        m2 = beta2*m2 + (1-beta2)*(g*g)
        m1h = m1/(1-beta1**k)
        m2h = m2/(1-beta2**k)
        step = lr * m1h / (np.sqrt(m2h) + eps)
        if verbose and k % 1000 == 0:
            print(f"[NN-Adam] iter {k:4d}  cost={hist[-1]:.6f}  ||step||={np.linalg.norm(step):.3e}")
        if np.linalg.norm(step) < tol:
            break
        theta = theta - step
    return theta, np.array(hist)



### Initialization and runs (NN)
We use small random weights. Compare GN+Armijo vs GD vs Adam.


In [ ]:
m = 8
W1 = 0.3*np.random.randn(m,1)
b1 = 0.1*np.random.randn(m)
w2 = 0.3*np.random.randn(m)
b2 = 0.0
theta0_nn = pack_nn(W1, b1, w2, b2)

theta_gn_nn, hist_gn_nn = gn_armijo_nn(theta0_nn, t, y, m, maxit=100, damping=1e-3, verbose=True)
theta_gd_nn, hist_gd_nn = gd_nn(theta0_nn, t, y, m, lr=1e-3, maxit=15000, verbose=True)
theta_adam_nn, hist_adam_nn = adam_nn(theta0_nn, t, y, m, lr=5e-3, maxit=15000, verbose=True)

def nn_predict(theta, t, m):
    W1, b1, w2, b2 = unpack_nn(theta, m)
    z = W1 @ t.reshape(1,-1) + b1.reshape(-1,1)
    h = np.tanh(z)
    return w2 @ h + b2

yhat_gn = nn_predict(theta_gn_nn, t, m)
yhat_gd = nn_predict(theta_gd_nn, t, m)
yhat_adam = nn_predict(theta_adam_nn, t, m)

plt.figure(figsize=(8,3))
plt.plot(t, y, '.', ms=2, label='y')
plt.plot(t, yhat_gn, label='NN GN+Armijo')
plt.plot(t, yhat_gd, label='NN GD')
plt.plot(t, yhat_adam, label='NN Adam')
plt.legend(); plt.title("NN fits (tanh)"); plt.show()

plt.figure(figsize=(6,3))
plt.semilogy(hist_gn_nn, label='NN GN+Armijo')
plt.semilogy(hist_gd_nn, label='NN GD')
plt.semilogy(hist_adam_nn, label='NN Adam')
plt.xlabel("iteration"); plt.ylabel("cost"); plt.title("NN convergence"); plt.legend(); plt.show()



## Takeaways & Future Work

- **GN + Armijo**: rapid local convergence when Jacobian is informative; Armijo improves robustness to poor inits.
- **GD**: simple and stable with small step; Armijo helps automate step-size selection.
- **Adam**: strong practical baseline; sometimes plateaus near the optimum vs GN's quadratic convergence.

**Future Work:**
1. **Levenberg–Marquardt**: Use $H_{LM}=J_r^\top J_r + \mu I$ with an adaptive $\mu$. Compare to GN + Armijo.
2. **Multi-tone extension**: For the sinusoid model, fit two sinusoids and discuss initialization.
3. **Activation variants**: Replace $\tanh$ with ReLU or GELU. Discuss smoothness and GN Jacobian behavior.
4. **Train/val split**: For the NN, track validation error and test different widths $m$ and weight decay (L2).
